## Getting distances between houses and schools in GeoPandas


Author: Robin Wilson

Email: robin@rtwilson.com

In [135]:
import pandas as pd
import geopandas as gpd
import shapely

In [136]:
# Read the house prices data - just using standard Pandas functions
houseprices = pd.read_csv("pp-2022.csv", header=None, usecols=[0, 1, 2, 3], names=['ID', 'Price', 'Date', 'Postcode'])

In [137]:
houseprices.head()

ID   Price              Date  Postcode
0  {DBA933F9-D5BC-669D-E053-6B04A8C0AD56}  205000  2022-02-18 00:00   DL9 4RS
1  {DBA933F9-D5BE-669D-E053-6B04A8C0AD56}  220000  2022-02-14 00:00  YO12 7ND
2  {DBA933F9-D5C0-669D-E053-6B04A8C0AD56}  775000  2022-02-22 00:00   HG5 0TT
3  {DBA933F9-D5C6-669D-E053-6B04A8C0AD56}  450000  2022-03-04 00:00  YO31 1BU
4  {DBA933F9-D5CC-669D-E053-6B04A8C0AD56}  175000  2022-02-25 00:00   LA2 7EB

In [138]:
# Read the postcodes data
postcodes = pd.read_csv("open_postcode_geo.csv/open_postcode_geo.csv", usecols=[0, 3, 4], names=['postcode', 'easting', 'northing'])

In [139]:
# Remove invalid data from the postcodes dataset
postcodes = postcodes[(postcodes.easting != "\\N") & (postcodes.northing != "\\N")]

In [140]:
# Subset down to just SO postcodes (Southampton/Hampshire area)
postcodes = postcodes[postcodes.postcode.str.startswith('SO')]

In [141]:
postcodes

postcode easting northing
2123582   SO1 0AA  442004   111235
2123583   SO1 0AB  441967   111272
2123584   SO1 0AD  441909   111317
2123585   SO1 0AE  441864   111334
2123586   SO1 0AF  441853   111406
...           ...     ...      ...
2164040  SO97 4AT  444918   116755
2164041  SO97 4AU  444918   116755
2164042  SO97 4AW  444918   116755
2164043  SO97 4AX  444918   116755
2164044  SO97 4AY  444918   116755

[40353 rows x 3 columns]

In [142]:
# Create a GeoDataFrame by taking the postcodes data and generating Shapely Point objects for the point locations
# and combining this with the original postcodes data in a new GeoDataFrame
# CRS = Co-ordinate Reference System (ie. projection). We set it to 27700 which is the EPSG code for the Ordnance Survey
# British National Grid
postcodes = gpd.GeoDataFrame(data=postcodes,
                             geometry=[shapely.geometry.Point(xy) for xy in zip(postcodes.easting, postcodes.northing)],
                             crs=27700)

In [143]:
# Read schools data
schools = pd.read_csv("edubasealldata20230920.csv", encoding='Windows-1252',
                      usecols=['URN', 'EstablishmentName', 'Easting', 'Northing', 'PhaseOfEducation (name)'])

In [144]:
# Subset to Primary schools
schools = schools[schools['PhaseOfEducation (name)'] == 'Primary']

In [145]:
schools

URN                           EstablishmentName  \
0      100000                          The Aldgate School   
8      100008                       Argyle Primary School   
9      100009               West Hampstead Primary School   
10     100010                    Brecknock Primary School   
11     100011                   Brookfield Primary School   
...       ...                                         ...   
47950  150361                     Heycroft Primary School   
47953  150365                   Field Place Infant School   
47954  150366                 Heckmondwike Primary School   
47955  150367                      Mallard Primary School   
47956  150368  Cranleigh Church of England Primary School   

      PhaseOfEducation (name)   Easting  Northing  
0                     Primary  533498.0  181201.0  
8                     Primary  530238.0  182761.0  
9                     Primary  524888.0  185067.0  
10                    Primary  529912.0  184835.0  
11                    Primary  528706.0  186594.0  
...                       ...       ...       ...  
47950                 Primary  584687.0  189038.0  
47953                 Primary  511692.0  103634.0  
47954                 Primary  422235.0  423602.0  
47955                 Primary  455577.0  400539.0  
47956                 Primary  505646.0  139372.0  

[29292 rows x 5 columns]

In [146]:
# Turn the schools data into a GeoDataFrame - just the same as we did with the postcodes above
schools = gpd.GeoDataFrame(data=schools,
                           geometry=[shapely.geometry.Point(xy) for xy in zip(schools.Easting, schools.Northing)],
                           crs=27700)

In [147]:
# Merge house prices with postcodes - just standard pandas functions here
houseprices = pd.merge(left=houseprices, right=postcodes, left_on='Postcode', right_on='postcode', how='inner')

In [148]:
# Turn this houseprices data into a GeoDataFrame
houseprices = gpd.GeoDataFrame(data=houseprices, geometry=houseprices.geometry, crs=27700)

In [149]:
# Run explore to get an interactive web map in the Jupyter notebook. Try hovering over one of the points!
houseprices.explore()

In [104]:
# Do the spatial join, here we are asking to join each row in houseprices with the nearest row in schools
# to get the nearest school for each house sale
joined = gpd.sjoin_nearest(houseprices, schools, distance_col='dist')

In [105]:
# Get some descriptive stats
joined.dist.describe()

count    14596.000000
mean       586.641433
std        453.603914
min          0.000000
25%        309.499999
50%        486.834146
75%        706.510439
max       5307.664835
Name: dist, dtype: float64